In [104]:
import csv
import json
from memoized import memoized
import xml.etree.ElementTree as et

@memoized
def loadjson(table_name):
  return json.load(open('/lfs/local/0/geza/ml-004_data_export/' + table_name + '.json'))

def get_table_path(table_name):
  csv_path = '/lfs/local/0/geza/ml-004_data_export/'
  return csv_path + table_name + '.csv'

def get_table_data(table_name):
  return csv.DictReader(open(get_table_path(table_name)), doublequote=False, delimiter=',', escapechar='\\')

def print_first_lines(table_name, n=10):
  for x in get_table_data(table_name):
    if n <= 0:
      break
    n -= 1
    print x

In [105]:
lecture_id_to_title = {}
lecture_title_to_id = {}

for line in get_table_data('lecture_metadata'):
  if line['deleted'] != '0':
    continue
  if line['final'] != '1':
    continue
  lecture_id = int(line['id'])
  if lecture_id > 114:
    continue
  title = line['title']
  lecture_id_to_title[lecture_id] = title
  if title in lecture_title_to_id:
    print 'duplicate:'
    print title
    print lecture_id
    print lecture_title_to_id[title]
    print line
  lecture_title_to_id[title] = lecture_id

In [106]:
#print lecture_id_to_title

In [107]:
quiz_id_to_lecture_title = {}

for line in get_table_data('quiz_metadata'):
  if line['deleted'] != '0':
    continue
  if line['duration'] != '0':
    continue
  quiz_id = int(line['id'])
  if quiz_id > 144:
    continue
  if line['quiz_type'] != 'video':
    continue
  title = line['title']
  quiz_id_to_lecture_title[quiz_id] = title

In [108]:
print len(quiz_id_to_lecture_title)

110


In [109]:
'''
#lecture_to_quiz_ids = {}
quiz_id_to_lecture_title = {}
quiz_id_to_xml = {}

for key,value in loadjson('kvs_course.quiz.xml'):
  try:
    parts = key.split('.')
    quiz_id = parts[1].split(':')[1]
    tree = et.fromstring(value.encode('utf-8'))
    title = list(tree.iter('title'))[0].text
    quiz_id_to_lecture_title[quiz_id] = title
    quiz_id_to_xml[quiz_id] = value
  except:
    continue
'''

"\n#lecture_to_quiz_ids = {}\nquiz_id_to_lecture_title = {}\nquiz_id_to_xml = {}\n\nfor key,value in loadjson('kvs_course.quiz.xml'):\n  try:\n    parts = key.split('.')\n    quiz_id = parts[1].split(':')[1]\n    tree = et.fromstring(value.encode('utf-8'))\n    title = list(tree.iter('title'))[0].text\n    quiz_id_to_lecture_title[quiz_id] = title\n    quiz_id_to_xml[quiz_id] = value\n  except:\n    continue\n"

In [110]:
#print quiz_id_to_lecture_title

In [111]:
#print lecture_title_to_id

In [112]:
lecture_id_to_quizzes = {}
quiz_to_lecture_id = {}

for quiz_id,lecture_title in quiz_id_to_lecture_title.items():
  if lecture_title not in lecture_title_to_id:
    print quiz_id
    print quiz_id_to_xml[quiz_id]
    continue
  lecture_id = lecture_title_to_id[lecture_title]
  if lecture_id not in lecture_id_to_quizzes:
    lecture_id_to_quizzes[lecture_id] = set()
  lecture_id_to_quizzes[lecture_id].add(quiz_id)
  quiz_to_lecture_id[quiz_id] = lecture_id


In [113]:
print lecture_id_to_quizzes

{2: set([2]), 3: set([3]), 4: set([4]), 5: set([5]), 6: set([6]), 7: set([7]), 9: set([9]), 10: set([10]), 11: set([11]), 13: set([21]), 14: set([22]), 15: set([23]), 16: set([24]), 17: set([25]), 18: set([26]), 19: set([27]), 20: set([28]), 21: set([29]), 22: set([30]), 23: set([31]), 24: set([32]), 25: set([33]), 26: set([34]), 27: set([35]), 28: set([36]), 29: set([37]), 30: set([38]), 31: set([39]), 32: set([40]), 33: set([41]), 34: set([42]), 35: set([43]), 36: set([44]), 37: set([45]), 38: set([46]), 39: set([47]), 40: set([48]), 41: set([49]), 42: set([50]), 43: set([51]), 44: set([52]), 45: set([53]), 46: set([54]), 47: set([55]), 48: set([56]), 49: set([57]), 50: set([58]), 51: set([59]), 52: set([60]), 53: set([61]), 54: set([62]), 55: set([63]), 56: set([64]), 57: set([65]), 58: set([72]), 59: set([76]), 60: set([77]), 61: set([78]), 62: set([79]), 63: set([80]), 64: set([81]), 65: set([82]), 66: set([83]), 67: set([84]), 68: set([85]), 69: set([86]), 70: set([87]), 71: set(

In [114]:
#print quiz_to_lecture_id

In [115]:
user_to_quizzes_submitted = {}
user_to_lectures_quizzes_submitted_for = {}

for line in get_table_data('quiz_submission_metadata'):
  user = line['session_user_id']
  quiz_id = int(line['item_id'])
  if user not in user_to_quizzes_submitted:
    user_to_quizzes_submitted[user] = set()
  user_to_quizzes_submitted[user].add(quiz_id)
  if quiz_id not in quiz_to_lecture_id:
    continue
  lecture_id = quiz_to_lecture_id[quiz_id]
  if user not in user_to_lectures_quizzes_submitted_for:
    user_to_lectures_quizzes_submitted_for[user] = set()
  user_to_lectures_quizzes_submitted_for[user].add(lecture_id)

In [116]:
user_to_lectures_viewed = {}

for line in get_table_data('lecture_submission_metadata'):
  action = line['action']
  user = line['session_user_id']
  lecture = line['item_id']
  submission_time = int(line['submission_time'])
  if submission_time > 1391185339: # newer than jan 31, 2014
    continue
  if action == 'view':
    if user not in user_to_lectures_viewed:
      user_to_lectures_viewed[user] = set()
    user_to_lectures_viewed[user].add(lecture)


In [117]:
user_to_lectures_finished = {}

for lecture_id,user_to_end_events in json.load(open('video_to_user_to_end_events.json')).iteritems():
  for user,end_events in user_to_end_events.iteritems():
    if user not in user_to_lectures_finished:
      user_to_lectures_finished[user] = []
    user_to_lectures_finished[user].append(lecture_id)


In [118]:
num_lectures_viewed = 0
num_lectures_finished = 0
num_lectures_for_which_quizzes_done = 0

for user,lectures_viewed in user_to_lectures_viewed.items():
  for lecture_id in lectures_viewed:
    lecture_id = int(lecture_id)
    if lecture_id not in lecture_id_to_quizzes:
      continue
    #quizzes = lecture_id_to_quizzes[lecture_id]
    num_lectures_viewed += 1
    if user in user_to_lectures_finished:
      if str(lecture_id) in user_to_lectures_finished[user]:
        num_lectures_finished += 1
    if user in user_to_lectures_quizzes_submitted_for:
      if lecture_id in user_to_lectures_quizzes_submitted_for[user]:
        num_lectures_for_which_quizzes_done += 1

In [119]:
print user_to_lectures_quizzes_submitted_for

{'abcea9860ecfb2fef5140bc9e504f529ed33eb39': set([2, 3, 4, 5, 6, 7, 9, 10, 11, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22]), '75298448184ce1d67cf2ae7197ee734eca6ffcab': set([2, 3, 4, 5, 6]), '870ab8b232bc52aaca8677bd64737f6e63057ac5': set([13, 14]), '5d5be0031d99d3f143b686c4693663b07136c8c7': set([3, 4, 5, 6, 7]), '816c15f84dd4246748117497e286a775a6c0b105': set([2, 3, 4, 5, 6, 7, 9, 10, 11, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 30, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 58, 59, 60, 61, 62, 63, 64, 71, 72, 73, 74, 75, 76, 77, 78]), 'e2a47cfb33d11ce05bad14b65fc043faa90e2748': set([2, 3, 4, 5, 6, 7, 9, 10, 11, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23]), '4dd6873f8f078db7162c7a25d9b0faf6b72b0b17': set([2]), 'c9e94ac3af8b86ace71d72065f03c8fb8403d897': set([2, 3, 4, 5, 6, 7, 104, 13, 14, 19, 20, 21]), 'b85c552750e5c91718a6a83c2722ab35f1eeec19': set([2, 3, 4, 5, 6, 7, 9, 10, 11, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 33, 34]), 

In [120]:
print num_lectures_viewed
print num_lectures_finished, num_lectures_finished/float(num_lectures_viewed)
print num_lectures_for_which_quizzes_done, num_lectures_for_which_quizzes_done/float(num_lectures_viewed)

1399037
917088 0.655513756963
1031770 0.737485856343


In [123]:
users_who_earned_certificate = set()

for line in get_table_data('course_grades'):
  user = line['session_user_id']
  if user not in user_to_lectures_viewed:
    continue
  grade = float(line['normal_grade'])
  if grade >= 80.0:
    users_who_earned_certificate.add(user)

In [124]:
num_lectures_viewed = 0
num_lectures_finished = 0
num_lectures_for_which_quizzes_done = 0

for user,lectures_viewed in user_to_lectures_viewed.items():
  if user not in users_who_earned_certificate:
    continue
  for lecture_id in lectures_viewed:
    lecture_id = int(lecture_id)
    if lecture_id not in lecture_id_to_quizzes:
      continue
    #quizzes = lecture_id_to_quizzes[lecture_id]
    num_lectures_viewed += 1
    if user in user_to_lectures_finished:
      if str(lecture_id) in user_to_lectures_finished[user]:
        num_lectures_finished += 1
    if user in user_to_lectures_quizzes_submitted_for:
      if lecture_id in user_to_lectures_quizzes_submitted_for[user]:
        num_lectures_for_which_quizzes_done += 1

In [125]:
print num_lectures_viewed
print num_lectures_finished, num_lectures_finished/float(num_lectures_viewed)
print num_lectures_for_which_quizzes_done, num_lectures_for_which_quizzes_done/float(num_lectures_viewed)

704859
504037 0.715089117114
557181 0.790485756726
